# Table of Contents
1. [Prerequisite](#Prerequisites)
    - [API Token Setup](##API-Token-Setup)
2. [Order Policies](##order-policies)
    - [Viewing Order Policies](###viewing-order-policies)
    - [Editing Order Policies](###editing-order-policies)
    - [Testing Endpoint Connection](###testing-endpoint-connection)
    - [Delete Order Policy](###delete-order-policy)
3. [Track Order](##track-orders)
    - [Searching for orders](###searching-for-orders)
    - [Searching for a Order](###Searching-for-a-Order)

## Prerequisites

In [ ]:
! python3 -m pip install tabulate

In [46]:
import requests
from tabulate import tabulate

# API Setup

Please enter your EDL authentication token below. This token will be used in the authorization header for all API requests.

If you do not have an EDL token, you can obtain one by visiting [urs website](https://uat.urs.earthdata.nasa.gov/).

In [48]:
url = 'https://cmr.uat.earthdata.nasa.gov/ordering/api'
token = 'Bearer your_edl_token'

# Order Policies

## Viewing Order Policies

#### API Query Setup

The following code snippet demonstrates how to make a GraphQL query to fetch provider policy details. 

#### Query
The `providerId` is required to perform the query. Replace `"MMT_2"` with the actual `providerId` you need to query.


In [50]:
# Configuration Section (provider_id is required)
provider_id = "MMT_2"

query = """
  query ProviderPolicy($providerId: String!) {
  providerPolicy(providerId: $providerId) {
    id
    providerId
    endpoint
    retryAttempts
    retryWaitTime
    orderingSuspendedUntilDate
    maxItemsPerOrder
    overrideNotifyEnabled
    referenceProps
    createdAt
    updatedAt
    sslPolicy {
      id
      providerPolicyId
      createdAt
      sslEnabled
      sslCertificate
      updatedAt
    }
  }
}
"""

# Variables
variables = {
  "providerId": provider_id
}

# Create a payload
payload = {
  "query": query,
  "variables": variables
}

headers = {
  "Content-Type": "application/json",
  "Authorization": token
}

response = requests.post(url, json=payload, headers=headers)

response_json = response.json()


if "errors" in response_json:
    error_message = response_json["errors"][0]["message"]
    print(f"Error encountered: {error_message}")
else:
    provider_policy_data = response_json['data']['providerPolicy']
    
    flat_data = {**provider_policy_data, **provider_policy_data['sslPolicy']}
    del flat_data['sslPolicy']

    # Convert the dictionary to a list of lists for tabulate
    table_data = [[key, value] for key, value in flat_data.items()]

    # Transpose and format the data into a table
    print(tabulate(table_data, headers=["Key", "Value"], tablefmt='fancy_grid'))

╒════════════════════════════╤════════════════════════════════════════════════════════╕
│ Key                        │ Value                                                  │
╞════════════════════════════╪════════════════════════════════════════════════════════╡
│ id                         │ 8cdf0fb4-9d50-4f1e-8fdd-d58162a71b36                   │
├────────────────────────────┼────────────────────────────────────────────────────────┤
│ providerId                 │ MMT_2                                                  │
├────────────────────────────┼────────────────────────────────────────────────────────┤
│ endpoint                   │ https://mmt.uat.earthdata.nasa.gov/order_policies/edit │
├────────────────────────────┼────────────────────────────────────────────────────────┤
│ retryAttempts              │ 3                                                      │
├────────────────────────────┼────────────────────────────────────────────────────────┤
│ retryWaitTime              │ 4

## Editing Order Policies

#### GraphQL Mutation Setup

The following code snippet demonstrates how to make a GraphQL mutation to update provider policy details. 

#### Mutation
The `providerId` is a required parameter for the mutation. Other parameters are optional and can be included based on your needs.

In [52]:
# Configuration Section (provider_id is required)
provider_id = "MMT_2"

# These values will have defaults and can be adjusted if needed
endpoint = "https://mmt.uat.earthdata.nasa.gov/order_policies/edit"
retry_attempts = 4
retry_wait_time = 4
ordering_suspended_until_date = None
max_items_per_order = 1000
reference_props = "Test Custom Policy"
override_notify_enabled = True
ssl_enabled= False
ssl_certificate= None

mutation = """
  mutation UpdateProviderPolicy($providerId: String!, $endpoint: String, $retryAttempts: Int, $retryWaitTime: Int, $orderingSuspendedUntilDate: Timestamp, $maxItemsPerOrder: Int, $referenceProps: String, $overrideNotifyEnabled: Boolean, $sslPolicy: SslPolicyInput) {
  updateProviderPolicy(providerId: $providerId, endpoint: $endpoint, retryAttempts: $retryAttempts, retryWaitTime: $retryWaitTime, orderingSuspendedUntilDate: $orderingSuspendedUntilDate, maxItemsPerOrder: $maxItemsPerOrder, referenceProps: $referenceProps, overrideNotifyEnabled: $overrideNotifyEnabled, sslPolicy: $sslPolicy) {
    id
    providerId
    endpoint
    retryAttempts
    retryWaitTime
    orderingSuspendedUntilDate
    maxItemsPerOrder
    overrideNotifyEnabled
    referenceProps
    sslPolicy {
      id
      providerPolicyId
      sslEnabled
      sslCertificate
      createdAt
      updatedAt
    }
    createdAt
    updatedAt
  }
}
"""

variables = {
  "providerId": provider_id,
  "endpoint":  endpoint,
  "retryAttempts": retry_attempts,
  "retryWaitTime": retry_wait_time,
  "orderingSuspendedUntilDate": ordering_suspended_until_date,
  "maxItemsPerOrder": max_items_per_order,
  "referenceProps": reference_props,
  "overrideNotifyEnabled": override_notify_enabled,
  "sslPolicy": {
    "sslEnabled": ssl_enabled,
    "sslCertificate": ssl_certificate
  }
}

# Create a payload
payload = {
  "query": mutation,
  "variables": variables
}

headers = {
  "Content-Type": "application/json",
  "Authorization": token
}

response = requests.post(url, json=payload, headers=headers)
response_json = response.json()

if "errors" in response_json:
    error_message = response_json["errors"][0]["message"]
    print(f"Error encountered: {error_message}")
else:
  update_provider_policy = response_json['data']['updateProviderPolicy']
  flat_data = {**update_provider_policy, **update_provider_policy['sslPolicy']}
  del flat_data['sslPolicy']

  # Convert the dictionary to a list of lists for tabulate
  table_data = [[key, value] for key, value in flat_data.items()]

  # Transpose and format the data into a table
  print(tabulate(table_data, headers=["Key", "Value"], tablefmt='fancy_grid'))

╒════════════════════════════╤════════════════════════════════════════════════════════╕
│ Key                        │ Value                                                  │
╞════════════════════════════╪════════════════════════════════════════════════════════╡
│ id                         │ 8cdf0fb4-9d50-4f1e-8fdd-d58162a71b36                   │
├────────────────────────────┼────────────────────────────────────────────────────────┤
│ providerId                 │ MMT_2                                                  │
├────────────────────────────┼────────────────────────────────────────────────────────┤
│ endpoint                   │ https://mmt.uat.earthdata.nasa.gov/order_policies/edit │
├────────────────────────────┼────────────────────────────────────────────────────────┤
│ retryAttempts              │ 4                                                      │
├────────────────────────────┼────────────────────────────────────────────────────────┤
│ retryWaitTime              │ 4

# Testing Endpoint Connection
#### GraphQL Mutation: Test Provider Connection

The following code snippet demonstrates how to make a GraphQL mutation to test the connection to a provider. 

### Mutation
The `providerId` is required for this mutation. This ID is used to test the connection for a specific provider.

In [54]:
# Configuration Section (provider_id is required)
provider_id = "MMT_2"

mutation = """
  mutation TestProviderConnection($providerId: String!) {
  testProviderConnection(providerId: $providerId) {
    requestId
    status
    statusMessage
  }
}
"""

# Variables
variables = {
  "providerId": provider_id
}

# Create a payload
payload = {
  "query": mutation,
  "variables": variables
}

headers = {
  "Content-Type": "application/json",
  "Authorization": token
}

response = requests.post(url, json=payload, headers=headers)
response_json = response.json()

if "errors" in response_json:
    error_message = response_json["errors"][0]["message"]
    print(f"Error encountered: {error_message}")
else:
  provider_policy_data = response_json['data']['testProviderConnection']
  
  table_data = [[key, value] for key, value in provider_policy_data.items()]

  print(tabulate(table_data, tablefmt='fancy_grid'))

╒═══════════════╤══════════════════════════════════════╕
│ requestId     │ 04775ed5-8170-43c4-8cd1-54b8d077fa67 │
├───────────────┼──────────────────────────────────────┤
│ status        │ 200                                  │
├───────────────┼──────────────────────────────────────┤
│ statusMessage │ OK                                   │
╘═══════════════╧══════════════════════════════════════╛


# Delete Order Policy
#### GraphQL Mutation: Delete Provider Policy

The following code snippet demonstrates how to make a GraphQL mutation to delete a provider policy.

### Mutation
The `providerId` is required for this mutation. This ID specifies which provider policy should be deleted.

### Example Mutation:
```graphql
mutation DeleteProviderPolicy($providerId: String!) {
  deleteProviderPolicy(providerId: $providerId)
}


In [ ]:
# Configuration Section (provider_id is required)
provider_id = "MMT_2"

mutation = """
  mutation DeleteProviderPolicy($providerId: String!) {
    deleteProviderPolicy(providerId: $providerId)
  }
"""

# Variables
variables = {
  "providerId": provider_id
}

# Create a payload
payload = {
  "query": mutation,
  "variables": variables
}

headers = {
  "Content-Type": "application/json",
  "Authorization": token
}

response = requests.post(url, json=payload, headers=headers)
response_json = response.json()

if "errors" in response_json:
    error_message = response_json["errors"][0]["message"]
    print(f"Error encountered: {error_message}")
else:
  provider_policy_data = response_json['data']['deleteProviderPolicy']
  
  table_data = [[key, value] for key, value in provider_policy_data.items()]

  print(tabulate(table_data, headers='keys', tablefmt='fancy_grid'))

# Track orders

### Searching for orders
##### GraphQL Query: Orders

The following code snippet demonstrates how to make a GraphQL query to fetch orders based on various parameters.

### Query
The `providerId` is a required parameter for this query. Other parameters are optional and can be used to filter the results based on specific criteria.

In [56]:
# Configuration Section (Only provider_id is required)
provider_id = "LPDAAC_TS1"  

# Optional Filters (default to None)
states = None # [VALIDATED, PENDING_SUBMISSION, SUBMITTING, SUBMIT_FAILED, SUBMIT_REJECTED, PROCESSING, CLOSED]
submitted_at = {"startDate": None, "endDate": None} # Dates in UTC format
created_at = {"startDate": None, "endDate": None}
updated_at = {"endDate": None}
urs_id = None

# Conditionally set variables
def get_value_if_not_all_none(data_dict):
    """Return the dictionary if not all values are None, otherwise return None."""
    if all(value is None for value in data_dict.values()):
        return None
    return data_dict

query = """
  query Orders($providerId: String!, $states: [OrderState], $submittedAt: DateRangeInput, $createdAt: DateRangeInput, $updatedAt: DateRangeInput, $ursId: String) {
  orders(providerId: $providerId, states: $states, submittedAt: $submittedAt, createdAt: $createdAt, updatedAt: $updatedAt, ursId: $ursId) {
    state
    createdAt
    submittedAt
    updatedAt
    contact {
      email
      firstName
      lastName
    }
    id
    providerTrackingId
  }
}
"""

# Variables
variables = {
  "providerId": provider_id,
  "states": states,
  "submittedAt": get_value_if_not_all_none(submitted_at),
  "createdAt": get_value_if_not_all_none(created_at),
  "updatedAt": get_value_if_not_all_none(updated_at),
  "ursId": urs_id
}

# Create a payload
payload = {
  "query": query,
  "variables": variables
}

headers = {
  "Content-Type": "application/json",
  "Authorization": token
}

response = requests.post(url, json=payload, headers=headers)

response_json = response.json()

if "errors" in response_json:
    error_message = response_json["errors"][0]["message"]
    print(f"Error encountered: {error_message}")
else:    
    orders_data = response_json['data']['orders']
    
    # Loop through each order and display
    for i, order in enumerate(orders_data):
        table_data = [[key, value] for key, value in order.items()]
        
        # Print the DataFrame using tabulate
        print(tabulate(table_data, tablefmt='fancy_grid'))

╒════════════════════╤═════════════════════════════════════════════════════════════════════════════════════════╕
│ state              │ SUBMIT_REJECTED                                                                         │
├────────────────────┼─────────────────────────────────────────────────────────────────────────────────────────┤
│ createdAt          │ 2023-05-09T14:53:20.642Z                                                                │
├────────────────────┼─────────────────────────────────────────────────────────────────────────────────────────┤
│ submittedAt        │ 2023-05-09T14:53:21.407Z                                                                │
├────────────────────┼─────────────────────────────────────────────────────────────────────────────────────────┤
│ updatedAt          │ 2023-05-09T14:53:21.409Z                                                                │
├────────────────────┼──────────────────────────────────────────────────────────────────────────

# Searching for a Order
#### GraphQL Query: Order

The following code snippet demonstrates how to make a GraphQL query to fetch details for a specific order based on the `orderId`.

### Query
The `orderId` is a required parameter for this query. This ID specifies which order details you want to retrieve.


In [58]:
# Configuration Section (Only orderId is required)
orderId = "718e6b19-d5a4-48d3-b72f-5fe9931b8426"  

query = """
  query Order($orderId: String!) {
  order(id: $orderId) {
    state
    createdAt
    submittedAt
    updatedAt
    contact {
      email
      firstName
      lastName
    }
    id
    providerTrackingId
  }
}
"""

# Variables
variables = {
  "orderId": orderId
}

# Create a payload
payload = {
  "query": query,
  "variables": variables
}

headers = {
  "Content-Type": "application/json",
  "Authorization": token
}

response = requests.post(url, json=payload, headers=headers)

response_json = response.json()

order_data = response_json['data']['order']

if "errors" in response_json:
    error_message = response_json["errors"][0]["message"]
    print(f"Error encountered: {error_message}")
else:
    table_data = [[key, value] for key, value in order_data.items()]
    
    print(tabulate(table_data, tablefmt='fancy_grid'))


╒════════════════════╤═════════════════════════════════════════════════════════════════════════════════╕
│ state              │ PROCESSING                                                                      │
├────────────────────┼─────────────────────────────────────────────────────────────────────────────────┤
│ createdAt          │ 2023-06-12T21:25:44.435Z                                                        │
├────────────────────┼─────────────────────────────────────────────────────────────────────────────────┤
│ submittedAt        │ 2023-06-12T21:40:49.428Z                                                        │
├────────────────────┼─────────────────────────────────────────────────────────────────────────────────┤
│ updatedAt          │ 2023-06-12T21:40:49.430Z                                                        │
├────────────────────┼─────────────────────────────────────────────────────────────────────────────────┤
│ contact            │ {'email': 'reit@contractor.usgs.

## Resubmitting Orders
#### GraphQL Query: Order

The following code snippet demonstrates how to make a GraphQL query to resubmit an order from a given order GUID.

### Query
The `resubmitOrderId` is a required parameter for this query. This ID specifies which order details you want to resubmit.

In [ ]:
# Configuration Section (Only resubmitOrderId is required)
resubmitOrderId = ""  

query = """
  mutation ResubmitOrder($resubmitOrderId: String!) {
  resubmitOrder(id: $resubmitOrderId) {
    id
    state
  }
}
"""

# Variables
variables = {
  "resubmitOrderId": resubmitOrderId
}

# Create a payload
payload = {
  "query": query,
  "variables": variables
}

headers = {
  "Content-Type": "application/json",
  "Authorization": token
}

response = requests.post(url, json=payload, headers=headers)

response_json = response.json()

resubmit_order = response_json['data']['resubmitOrder']

if "errors" in response_json:
    error_message = response_json["errors"][0]["message"]
    print(f"Error encountered: {error_message}")
else:
    table_data = [[key, value] for key, value in resubmit_order.items()]
    
    print(tabulate(table_data, tablefmt='fancy_grid'))